In [1]:
import pandas as pd
import numpy as np 
import tensorflow as tf
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import train_test_split
from sklearn import metrics
from datetime import datetime
from sklearn.naive_bayes import GaussianNB
from sklearn import tree
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression

In [2]:
df = pd.read_csv('fservice.csv')

/Users/andyhan/miniconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3072: DtypeWarning: Columns (20,33) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
c = ['Anonymous','AssignTo', 'RequestType', 'RequestSource','CD','Direction', 'ActionTaken', 'APC' ,'AddressVerified']
d = ['Latitude', 'Longitude']

# Feature cleaning

In [4]:
dfn = df.filter(items = c + d + ['ElapsedDays'] + ['Seven'])
dfn = dfn.dropna()
    
XCAT = dfn.filter(items = c).values
XNUM = dfn.filter(items = d).values
    
y = dfn['ElapsedDays'] <= 7
    
labelencoder_X = LabelEncoder()
for num in range(len(c)): 
    XCAT[:, num] = labelencoder_X.fit_transform(XCAT[:, num])
            
onehotencoder = OneHotEncoder()
XCAT = onehotencoder.fit_transform(XCAT).toarray()
    
X = np.concatenate((XCAT, XNUM), axis=1)

XN = X[:10]
yn = y[:10]

X = X[10:]
y = y[10:]

In [7]:
# Change y-values to numbers
y = pd.get_dummies(y)
y = y.drop(columns=False)

# Building neural network

In [5]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 0)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size = 0.2, random_state = 0)

In [6]:
X_train = np.asarray(X_train)
y_train = np.asarray(y_train)
X_val = np.asarray(X_val)
y_val = np.asarray(y_val)

# should we normalize the latitude / longitude?

In [10]:
# Initialize model
model = tf.keras.Sequential()  # i think this is a simple feed-forward?
# three hidden layers for now
model.add(tf.keras.layers.Dense(128, activation=tf.nn.relu))
model.add(tf.keras.layers.Dense(128, activation=tf.nn.relu))
model.add(tf.keras.layers.Dense(128, activation=tf.nn.relu))
model.add(tf.keras.layers.Dense(1, activation=tf.nn.sigmoid))

# Compile model
model.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['accuracy'])

# Fit model
model.fit(X_train, y_train, epochs=3)

Train on 1980678 samples
Epoch 1/3
1980678/1980678 [==============================] - 232s 117us/sample - loss: 0.1958 - accuracy: 0.9342
Epoch 2/3
1980678/1980678 [==============================] - 215s 109us/sample - loss: 0.1924 - accuracy: 0.9354
Epoch 3/3
1980678/1980678 [==============================] - 215s 109us/sample - loss: 0.1916 - accuracy: 0.9358


In [11]:
#Test model
val_loss, val_acc = model.evaluate(X_val, y_val)
print(val_loss, val_acc)

# y_vpred = classifier.predict(X_val)

#Print Accuracy Function results
# print("Accuracy:",metrics.accuracy_score(y_val, y_vpred))
# print("Precision, Recall, F1Score:",metrics.precision_recall_fscore_support(y_val, y_vpred, average = 'binary'))

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



0.19140696629188517 0.9356019


In [12]:
y_tpred = classifier.predict(X_test)

#Print Accuracy Function results

print("Accuracy:",metrics.accuracy_score(y_test, y_tpred))
print("Precision, Recall, F1Score:",metrics.precision_recall_fscore_support(y_test, y_tpred, average = 'binary'))

NameError: name 'classifier' is not defined

# Hyperparameter Tuning

In [7]:
import kerastuner

In [8]:
# down-sample data to 10% of original
mask = np.random.choice([False, True], len(X_train), p=[0.9, 0.1])
X_train_small = X_train[mask]
y_train_small = y_train[mask]

In [9]:
# build hypermodel, containing different choices for various hyperparameters

class thisHyperModel(kerastuner.HyperModel):
    
    def build(self, hp):
        model = tf.keras.Sequential()
        # 5 hidden layers
        model.add(tf.keras.layers.Dense(
                                    units=hp.Int(
                                        'units',
                                        min_value=16,
                                        max_value=256,
                                        step=32,
                                        default=128
                                    ),
                                    activation=hp.Choice(
                                        'dense_activation',
                                        values=['relu', 'tanh', 'sigmoid'],
                                        default='relu')
                                )
                    )
        model.add(tf.keras.layers.Dense(
                                    units=hp.Int(
                                        'units',
                                        min_value=16,
                                        max_value=256,
                                        step=32,
                                        default=128
                                    ),
                                    activation=hp.Choice(
                                        'dense_activation',
                                        values=['relu', 'tanh', 'sigmoid'],
                                        default='relu')
                                )
                    )
        model.add(tf.keras.layers.Dense(
                                    units=hp.Int(
                                        'units',
                                        min_value=16,
                                        max_value=256,
                                        step=32,
                                        default=128
                                    ),
                                    activation=hp.Choice(
                                        'dense_activation',
                                        values=['relu', 'tanh', 'sigmoid'],
                                        default='relu')
                                )
                    )
        model.add(tf.keras.layers.Dense(
                                    units=hp.Int(
                                        'units',
                                        min_value=16,
                                        max_value=256,
                                        step=32,
                                        default=128
                                    ),
                                    activation=hp.Choice(
                                        'dense_activation',
                                        values=['relu', 'tanh', 'sigmoid'],
                                        default='relu')
                                )
                    )
        model.add(tf.keras.layers.Dense(
                                    units=hp.Int(
                                        'units',
                                        min_value=16,
                                        max_value=256,
                                        step=32,
                                        default=128
                                    ),
                                    activation=hp.Choice(
                                        'dense_activation',
                                        values=['relu', 'tanh', 'sigmoid'],
                                        default='relu')
                                )
                    )
        model.add(tf.keras.layers.Dense(1, activation=tf.nn.sigmoid))
        
        model.compile(
            optimizer=tf.keras.optimizers.Adam(
                hp.Float(
                    'learning_rate',
                    min_value=1e-4,
                    max_value=1e-2,
                    sampling='LOG',
                    default=1e-3
                )
            ),
            loss='binary_crossentropy',
            metrics=['accuracy']
        )
        return model

In [10]:
hypermodel = thisHyperModel()

In [11]:
HYPERBAND_MAX_EPOCHS = 20
MAX_TRIALS = 20
EXECUTION_PER_TRIAL = 1
SEED = 47

In [12]:
# define the tuner

tuner = kerastuner.tuners.Hyperband(
    hypermodel,
    max_epochs=HYPERBAND_MAX_EPOCHS,
    objective='val_accuracy',
    seed=SEED,
    hyperband_iterations=EXECUTION_PER_TRIAL
)

INFO:tensorflow:Reloading Oracle from existing project ./untitled_project/oracle.json
INFO:tensorflow:Reloading Tuner from ./untitled_project/tuner0.json


In [13]:
tuner.search_space_summary()

In [ ]:
# run the tuner. takes fOrEvErrr aigoo
N_EPOCH_SEARCH=40
tuner.search(X_train_small, y_train_small, validation_split=0.1)

Train on 178506 samples, validate on 19835 samples
Epoch 15/40


 62528/178506 [=========>....................] - ETA: 2:14:07 - loss: 0.2698 - accuracy: 0.937 - ETA: 17:20 - loss: 0.2558 - accuracy: 0.9414  - ETA: 7:58 - loss: 0.2077 - accuracy: 0.951 - ETA: 5:05 - loss: 0.2418 - accuracy: 0.94 - ETA: 3:48 - loss: 0.2636 - accuracy: 0.93 - ETA: 3:08 - loss: 0.2665 - accuracy: 0.93 - ETA: 2:38 - loss: 0.2775 - accuracy: 0.92 - ETA: 2:18 - loss: 0.2911 - accuracy: 0.92 - ETA: 2:04 - loss: 0.2828 - accuracy: 0.92 - ETA: 1:52 - loss: 0.2834 - accuracy: 0.92 - ETA: 1:43 - loss: 0.2848 - accuracy: 0.92 - ETA: 1:35 - loss: 0.2817 - accuracy: 0.92 - ETA: 1:30 - loss: 0.2777 - accuracy: 0.92 - ETA: 1:26 - loss: 0.2768 - accuracy: 0.92 - ETA: 1:21 - loss: 0.2777 - accuracy: 0.92 - ETA: 1:17 - loss: 0.2714 - accuracy: 0.92 - ETA: 1:14 - loss: 0.2744 - accuracy: 0.92 - ETA: 1:11 - loss: 0.2742 - accuracy: 0.92 - ETA: 1:08 - loss: 0.2728 - accuracy: 0.92 - ETA: 1:06 - loss: 0.2745 - accuracy: 0.92 - ETA: 1:04 - loss: 0.2747 - accuracy: 0.92 - ETA: 1:02 - loss: 

121280/178506 [===================>..........] - ETA: 20s - loss: 0.2225 - accuracy: 0.929 - ETA: 20s - loss: 0.2224 - accuracy: 0.929 - ETA: 20s - loss: 0.2226 - accuracy: 0.929 - ETA: 20s - loss: 0.2226 - accuracy: 0.929 - ETA: 20s - loss: 0.2225 - accuracy: 0.929 - ETA: 19s - loss: 0.2223 - accuracy: 0.929 - ETA: 19s - loss: 0.2225 - accuracy: 0.929 - ETA: 19s - loss: 0.2225 - accuracy: 0.929 - ETA: 19s - loss: 0.2220 - accuracy: 0.929 - ETA: 19s - loss: 0.2220 - accuracy: 0.929 - ETA: 19s - loss: 0.2218 - accuracy: 0.929 - ETA: 19s - loss: 0.2215 - accuracy: 0.929 - ETA: 19s - loss: 0.2210 - accuracy: 0.929 - ETA: 19s - loss: 0.2212 - accuracy: 0.929 - ETA: 19s - loss: 0.2212 - accuracy: 0.929 - ETA: 19s - loss: 0.2213 - accuracy: 0.929 - ETA: 19s - loss: 0.2214 - accuracy: 0.929 - ETA: 19s - loss: 0.2210 - accuracy: 0.929 - ETA: 19s - loss: 0.2210 - accuracy: 0.929 - ETA: 19s - loss: 0.2209 - accuracy: 0.929 - ETA: 18s - loss: 0.2209 - accuracy: 0.929 - ETA: 18s - loss: 0.2206 - a

178016/178506 [============================>.] - ETA: 9s - loss: 0.2146 - accuracy: 0.93 - ETA: 9s - loss: 0.2145 - accuracy: 0.93 - ETA: 9s - loss: 0.2146 - accuracy: 0.93 - ETA: 9s - loss: 0.2147 - accuracy: 0.93 - ETA: 9s - loss: 0.2147 - accuracy: 0.93 - ETA: 9s - loss: 0.2147 - accuracy: 0.93 - ETA: 9s - loss: 0.2147 - accuracy: 0.93 - ETA: 9s - loss: 0.2146 - accuracy: 0.93 - ETA: 9s - loss: 0.2146 - accuracy: 0.93 - ETA: 9s - loss: 0.2145 - accuracy: 0.93 - ETA: 9s - loss: 0.2145 - accuracy: 0.93 - ETA: 9s - loss: 0.2144 - accuracy: 0.93 - ETA: 9s - loss: 0.2143 - accuracy: 0.93 - ETA: 9s - loss: 0.2142 - accuracy: 0.93 - ETA: 8s - loss: 0.2141 - accuracy: 0.93 - ETA: 8s - loss: 0.2140 - accuracy: 0.93 - ETA: 8s - loss: 0.2141 - accuracy: 0.93 - ETA: 8s - loss: 0.2140 - accuracy: 0.93 - ETA: 8s - loss: 0.2141 - accuracy: 0.93 - ETA: 8s - loss: 0.2140 - accuracy: 0.93 - ETA: 8s - loss: 0.2139 - accuracy: 0.93 - ETA: 8s - loss: 0.2138 - accuracy: 0.93 - ETA: 8s - loss: 0.2137 - ac

178506/178506 [==============================] - ETA: 0s - loss: 0.2109 - accuracy: 0.93 - 33s 183us/sample - loss: 0.2109 - accuracy: 0.9308 - val_loss: 0.1991 - val_accuracy: 0.9322
Epoch 16/40


...

 48096/178506 [=======>......................] - ETA: 41s - loss: 0.1704 - accuracy: 0.906 - ETA: 28s - loss: 0.1587 - accuracy: 0.945 - ETA: 27s - loss: 0.1516 - accuracy: 0.949 - ETA: 27s - loss: 0.1643 - accuracy: 0.946 - ETA: 27s - loss: 0.1738 - accuracy: 0.943 - ETA: 27s - loss: 0.1708 - accuracy: 0.943 - ETA: 27s - loss: 0.1656 - accuracy: 0.946 - ETA: 27s - loss: 0.1723 - accuracy: 0.944 - ETA: 26s - loss: 0.1702 - accuracy: 0.945 - ETA: 26s - loss: 0.1718 - accuracy: 0.945 - ETA: 26s - loss: 0.1725 - accuracy: 0.944 - ETA: 26s - loss: 0.1786 - accuracy: 0.941 - ETA: 26s - loss: 0.1762 - accuracy: 0.942 - ETA: 26s - loss: 0.1778 - accuracy: 0.942 - ETA: 26s - loss: 0.1787 - accuracy: 0.942 - ETA: 26s - loss: 0.1763 - accuracy: 0.942 - ETA: 26s - loss: 0.1776 - accuracy: 0.941 - ETA: 26s - loss: 0.1780 - accuracy: 0.941 - ETA: 26s - loss: 0.1787 - accuracy: 0.941 - ETA: 26s - loss: 0.1797 - accuracy: 0.940 - ETA: 26s - loss: 0.1782 - accuracy: 0.940 - ETA: 26s - loss: 0.1813 - a

 73728/178506 [===========>..................] - ETA: 1:31:24 - loss: 0.1890 - accuracy: 0.936 - ETA: 1:30:40 - loss: 0.1889 - accuracy: 0.936 - ETA: 1:29:56 - loss: 0.1893 - accuracy: 0.936 - ETA: 1:29:08 - loss: 0.1891 - accuracy: 0.936 - ETA: 1:28:25 - loss: 0.1893 - accuracy: 0.936 - ETA: 1:27:47 - loss: 0.1893 - accuracy: 0.936 - ETA: 1:27:15 - loss: 0.1895 - accuracy: 0.936 - ETA: 1:26:43 - loss: 0.1894 - accuracy: 0.936 - ETA: 1:26:06 - loss: 0.1894 - accuracy: 0.936 - ETA: 1:25:30 - loss: 0.1892 - accuracy: 0.936 - ETA: 1:24:54 - loss: 0.1892 - accuracy: 0.936 - ETA: 1:24:23 - loss: 0.1892 - accuracy: 0.936 - ETA: 1:23:48 - loss: 0.1892 - accuracy: 0.936 - ETA: 1:23:09 - loss: 0.1892 - accuracy: 0.936 - ETA: 1:22:30 - loss: 0.1894 - accuracy: 0.936 - ETA: 1:21:56 - loss: 0.1893 - accuracy: 0.936 - ETA: 1:21:18 - loss: 0.1892 - accuracy: 0.936 - ETA: 1:20:40 - loss: 0.1892 - accuracy: 0.936 - ETA: 1:20:03 - loss: 0.1891 - accuracy: 0.936 - ETA: 1:19:27 - loss: 0.1891 - accuracy:

 79424/178506 [============>.................] - ETA: 48:35 - loss: 0.1938 - accuracy: 0.934 - ETA: 48:33 - loss: 0.1938 - accuracy: 0.934 - ETA: 48:31 - loss: 0.1938 - accuracy: 0.934 - ETA: 48:29 - loss: 0.1938 - accuracy: 0.934 - ETA: 48:27 - loss: 0.1938 - accuracy: 0.934 - ETA: 48:25 - loss: 0.1938 - accuracy: 0.934 - ETA: 48:22 - loss: 0.1938 - accuracy: 0.934 - ETA: 48:20 - loss: 0.1938 - accuracy: 0.934 - ETA: 48:18 - loss: 0.1939 - accuracy: 0.934 - ETA: 48:16 - loss: 0.1940 - accuracy: 0.934 - ETA: 48:14 - loss: 0.1939 - accuracy: 0.934 - ETA: 48:12 - loss: 0.1940 - accuracy: 0.934 - ETA: 48:10 - loss: 0.1940 - accuracy: 0.934 - ETA: 48:08 - loss: 0.1940 - accuracy: 0.934 - ETA: 48:06 - loss: 0.1940 - accuracy: 0.934 - ETA: 48:04 - loss: 0.1940 - accuracy: 0.934 - ETA: 48:02 - loss: 0.1940 - accuracy: 0.934 - ETA: 48:00 - loss: 0.1940 - accuracy: 0.934 - ETA: 47:58 - loss: 0.1940 - accuracy: 0.934 - ETA: 47:56 - loss: 0.1941 - accuracy: 0.934 - ETA: 47:54 - loss: 0.1941 - acc

 85120/178506 [=============>................] - ETA: 42:54 - loss: 0.1941 - accuracy: 0.934 - ETA: 42:52 - loss: 0.1941 - accuracy: 0.934 - ETA: 42:50 - loss: 0.1940 - accuracy: 0.935 - ETA: 42:48 - loss: 0.1940 - accuracy: 0.935 - ETA: 42:47 - loss: 0.1939 - accuracy: 0.935 - ETA: 42:45 - loss: 0.1939 - accuracy: 0.935 - ETA: 42:43 - loss: 0.1939 - accuracy: 0.935 - ETA: 42:41 - loss: 0.1939 - accuracy: 0.935 - ETA: 42:40 - loss: 0.1939 - accuracy: 0.935 - ETA: 42:38 - loss: 0.1938 - accuracy: 0.935 - ETA: 42:36 - loss: 0.1938 - accuracy: 0.935 - ETA: 42:34 - loss: 0.1938 - accuracy: 0.935 - ETA: 42:33 - loss: 0.1938 - accuracy: 0.935 - ETA: 42:31 - loss: 0.1937 - accuracy: 0.935 - ETA: 42:29 - loss: 0.1937 - accuracy: 0.935 - ETA: 42:27 - loss: 0.1938 - accuracy: 0.935 - ETA: 42:26 - loss: 0.1938 - accuracy: 0.935 - ETA: 42:24 - loss: 0.1938 - accuracy: 0.935 - ETA: 42:22 - loss: 0.1938 - accuracy: 0.935 - ETA: 42:20 - loss: 0.1938 - accuracy: 0.935 - ETA: 42:19 - loss: 0.1938 - acc

 89664/178506 [==============>...............] - ETA: 37:58 - loss: 0.1937 - accuracy: 0.935 - ETA: 37:57 - loss: 0.1937 - accuracy: 0.935 - ETA: 37:55 - loss: 0.1937 - accuracy: 0.935 - ETA: 37:53 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:52 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:50 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:49 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:47 - loss: 0.1937 - accuracy: 0.935 - ETA: 37:46 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:44 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:43 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:41 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:39 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:38 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:36 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:35 - loss: 0.1938 - accuracy: 0.935 - ETA: 37:33 - loss: 0.1937 - accuracy: 0.935 - ETA: 37:32 - loss: 0.1937 - accuracy: 0.935 - ETA: 37:30 - loss: 0.1937 - accuracy: 0.935 - ETA: 37:29 - loss: 0.1936 - accuracy: 0.935 - ETA: 37:27 - loss: 0.1937 - acc